In [1]:
# Import the Earth Engine library.
import ee
import geemap
import pandas as pd

ee.Initialize()

In [2]:
## copy and paste raw url from github repo.
station_lat = 22.59
station_lon = 89.46
path = r"E:\Script\Google_Earth_Engine\tides_2022_11_22.csv"
df = pd.read_csv(path, names=['date', 'tides'])
print(df.head(5))

         date     tides
0  11/22/2012  0.188058
1  11/23/2012  0.499850
2  11/24/2012  0.668436
3  11/25/2012  0.689802
4  11/26/2012  0.587833


In [3]:
## add the lon lat coordinates to the dataframe
from datetime import datetime
df['lon'] = station_lon
df['lat'] = station_lat
df["date"] = df["date"].astype('datetime64[ns]').astype(str)
df

date     tides    lon    lat
0     2012-11-22  0.188058  89.46  22.59
1     2012-11-23  0.499850  89.46  22.59
2     2012-11-24  0.668436  89.46  22.59
3     2012-11-25  0.689802  89.46  22.59
4     2012-11-26  0.587833  89.46  22.59
...          ...       ...    ...    ...
3649  2022-11-19  0.597187  89.46  22.59
3650  2022-11-20  0.784154  89.46  22.59
3651  2022-11-21  0.846214  89.46  22.59
3652  2022-11-22  0.745477  89.46  22.59
3653  2022-11-23  0.475521  89.46  22.59

[3654 rows x 4 columns]

In [4]:
## convert to an earth engine object.
from geemap.common import df_to_ee

gee_df = df_to_ee(df, latitude='lat', longitude='lon')
gee_df

In [5]:
# tide guage location point
first_point = ee.Feature(gee_df.first())

# Add the AOI to the Map.
Map = geemap.Map(center=[station_lat, station_lon], zoom=11, height=400, draw = True)
Map.add_basemap("SATELLITE")
Map.addLayer(first_point, {'color':'red'}, "Tide point")
Map

Map(center=[22.59, 89.46], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(childre…

In [6]:
# Taking a draw feature from the map.
feature = Map.draw_last_feature

# If drawing does not exist then taking a polygon as the default version.
if feature is None:
    geom = ee.Geometry.Polygon([[[91.78481923595828, 21.95584672623341],
                                 [91.78481923595828, 21.700881280747268],
                                 [91.93176137463016, 21.700881280747268],
                                 [91.93176137463016, 21.95584672623341]]])
    feature = ee.Feature(geom, {})

# Define the AOI.
AOI = feature.geometry()

# Visualize the map.
Map.addLayer(AOI, {}, "AOI")
Map

Map(bottom=228558.0, center=[22.59, 89.46], controls=(WidgetControl(options=['position', 'transparent_bg'], wi…

In [7]:
# This function returns a masked sentinel-2 collection.
def get_cloud_masked_s2(start_date, end_date, AOI, cloud_threshold):
  # Get the sentinel-2 collection, filter by date and geometry.
  s2 = ee.ImageCollection("COPERNICUS/S2_HARMONIZED").filter([
           ee.Filter.date(start_date, end_date),
           ee.Filter.bounds(AOI)])

  # Get the cloudless collection.
  s2_cloudless = ee.ImageCollection("COPERNICUS/S2_CLOUD_PROBABILITY").filter([
            ee.Filter.date(start_date, end_date),
            ee.Filter.bounds(AOI)])

  # join the two collections together.
  join = ee.Join.inner().apply(**{
        'primary': s2,
        'secondary': s2_cloudless,
        'condition': ee.Filter.equals(**{'leftField': 'system:index','rightField': 'system:index'})})

  ## reformat it back to an image collection.
  merged = ee.ImageCollection(
      join.map(lambda feature: ee.Image(feature.get('primary')).addBands(feature.get('secondary'))))

  # apply the cloud masking.
  cloud_masked = merged.map(
    lambda image: image.updateMask(image.select('probability').lt(cloud_threshold)))

  # Return a cloud masked image.
  return cloud_masked


In [31]:
s2_collection = (get_cloud_masked_s2(
    start_date = '2022-09-01',
    end_date = '2022-12-31',
    AOI = AOI, ##intersects with our point
    cloud_threshold = 50
    ))

# Create a median image for visualisation and clip to geometry.
s2_median = s2_collection.median().clip(AOI)

In [32]:
# Add the AOI to the Map.
Map = geemap.Map(center=[station_lat, station_lon], zoom=11, height=500, draw = True)
Map.add_basemap("TERRAIN")
Map.addLayer(s2_median, {'bands': ['B12', 'B8', 'B3'], 'min': 0, 'max': 3000},'s2 RGB median')
Map.addLayer(first_point, {'color':'red'}, "Tide point")
Map

Map(center=[22.59, 89.46], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(childre…

In [33]:
# First add a time property in the same format as our tide data: YYYY-MM-dd'
s2_collection = s2_collection.map(
    lambda image: image.set('time', image.date().format('YYYY-MM-dd'))
    )

# Lots of info... bands, id, and at the bottom is our new attribute.
s2_collection.first()

In [34]:
# Join the imagery to the tides by time property.
time_filter = ee.Filter.equals(leftField= 'time', rightField= 'date')
inner_join = ee.Join.inner()

# The join returns a feature collection with primary being s2 image, and secondary being date.
joined = inner_join.apply(s2_collection, gee_df, time_filter)

# Let's reformat that back to an image collection with the tides as attribute.
def tides_as_attribute (joined):
  image = ee.Image(joined.get('primary'))
  tide = ee.Feature(joined.get('secondary')).get('tides')
  return image.set('tide', tide)

# Apply the function.
tide_collection = ee.ImageCollection(joined.map(tides_as_attribute))

tide_collection.size().getInfo()

70

In [35]:
tide_collection.first()

In [36]:
tide_collection.aggregate_stats('tide')

In [37]:
# +/- 1 standard deviation
stats = tide_collection.aggregate_stats('tide')
mean = stats.getNumber('mean')
sd = stats.getNumber('total_sd')

print(
 f" mean ({mean.format('%.2f').getInfo()}) +/- 1 standard deviation \
 ({sd.format('%.2f').getInfo()}) = \
 {mean.subtract(sd).format('%.2f').getInfo()} to \
 {mean.add(sd).format('%.2f').getInfo()}"
)

 mean (-0.05) +/- 1 standard deviation  (0.69) =  -0.74 to  0.64


In [38]:
high_tide_threshold = 0.64
low_tide_threshold = -0.74

In [39]:
high_tide_collection = tide_collection.filter(ee.Filter.gt('tide', high_tide_threshold))
low_tide_collection = tide_collection.filter(ee.Filter.lt('tide', low_tide_threshold))

high_tide_size = high_tide_collection.size().getInfo()
low_tide_size = low_tide_collection.size().getInfo()

print(f'\
Number of images in the high tide collection {high_tide_size} \n\
Number of images in the low tide collection {low_tide_size}'
)

Number of images in the high tide collection 20 
Number of images in the low tide collection 18


In [40]:
# Get filtered medians.
high_tide_median = high_tide_collection.median().clip(AOI)
low_tide_median = low_tide_collection.median().clip(AOI)

# Add the AOI to the Map.
Map = geemap.Map(center=[station_lat, station_lon], zoom=12, height=500, draw = True)
Map.add_basemap("TERRAIN")
left_layer = geemap.ee_tile_layer(high_tide_median, {'bands': ['B12', 'B8', 'B3'], 'min': 0, 'max': 2000}, 'High tide median')
right_layer = geemap.ee_tile_layer(low_tide_median, {'bands': ['B12', 'B8', 'B3'], 'min': 0, 'max': 2000}, 'Low tide median')
Map.split_map(left_layer, right_layer)
Map

Map(center=[22.59, 89.46], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_o…

In [41]:
# Exporting 'HIGH TIDE' image to google drive
task = ee.batch.Export.image.toDrive(
            image = high_tide_median.select(["B12","B8","B3"]).uint16(),
            description = 'Sentinel_2_HT_2022',
            folder = 'Tide_Corrected_Image',
            crs = 'EPSG:32645', # UTM 45N
            scale = 10,
            maxPixels = 10e12,
            fileDimensions= 256*2*100,
            shardSize= 256*2,
            formatOptions = {'cloudOptimized': True})

task.start()

In [42]:
# Exporting 'LOW TIDE' image to google drive
task = ee.batch.Export.image.toDrive(
            image = low_tide_median.select(["B12","B8","B3"]).uint16(),
            description = 'Sentinel_2_LT_2022',
            folder = 'Tide_Corrected_Image',
            crs = 'EPSG:32645', # UTM 45N
            scale = 10,
            maxPixels = 10e12,
            fileDimensions= 256*2*100,
            shardSize= 256*2,
            formatOptions = {'cloudOptimized': True})

task.start()